# Workshop: Leveraging Non-traditional Sources of Data in Public Health Informatics

Still in development.

Author: Adrien Carrel

In [3]:
import os
import pandas as pd
import numpy as np
import plotly.graph_objects as go

## Data Exploration

Task 0: Download some Google Trends data using the get_data function below.

In [ ]:
from pytrends.exceptions import ResponseError
from pytrends.request import TrendReq as UTrendReq
from datetime import date, timedelta
from functools import partial
from time import sleep
from calendar import monthrange

GET_METHOD = "get"


class TrendReq(UTrendReq):
    """
    Child class of pytrends' TrendReq
    This allows to change the header to avoid 429 errors

    Source: https://stackoverflow.com/questions/50571317/pytrends-the-request-failed-google-returned-a-response-with-code-429

    Args:
        UTrendReq (TrendReq): native TrendReq object from pytrends
    """

    def _get_data(self, url, method=GET_METHOD, trim_chars=0, **kwargs):
        return super()._get_data(
            url, method=GET_METHOD, trim_chars=trim_chars,  # headers=headers,
            **kwargs
        )


def get_last_date_of_month(year: int, month: int) -> date:
    """
    Given a year and a month returns an instance of the date class
    containing the last day of the corresponding month.

    Source: https://stackoverflow.com/questions/42950/get-last-day-of-the-month-in-python

    Args:
        year (int): year
        month (int): month

    Returns:
        date: last day of the month
    """

    return date(year, month, monthrange(year, month)[1])


def convert_dates_to_timeframe(start: date, stop: date) -> str:
    """
    Given two dates, returns a stringified version of the interval between
    the two dates which is used to retrieve data for a specific time frame
    from Google Trends.

    Args:
        start (date): start date datetime format
        stop (date): stop date datetime format

    Returns:
        str: combination of the two dates in Y-M-D format
    """
    return f"{start.strftime('%Y-%m-%d')} {stop.strftime('%Y-%m-%d')}"


def _fetch_data(pytrends, build_payload, timeframe: str) -> pd.DataFrame:
    """
    Attempts to fecth data and retries in case of a ResponseError.

    Args:
        pytrends (TrendReq): TrendReq pytrends object with a _get_data
            method
        build_payload (build_payload): build_payload pytrends object loaded on
            a set of keywords
        timeframe (str): google trends timeframe format to fetch data

    Returns:
        pd.DataFrame: interest over time
    """
    attempts, fetched = 0, False
    while not fetched:
        try:
            build_payload(timeframe=timeframe)
        except ResponseError as err:
            print(err)
            print(f"Trying again in {60 + 5 * attempts} seconds.")
            sleep(60 + 5 * attempts)
            attempts += 1
            if attempts > 3:
                print("Failed after 3 attemps, abort fetching.")
                break
        else:
            fetched = True
    return pytrends.interest_over_time()


def get_data(
    word: str,
    start_year: int,
    start_mon: int,
    stop_year: int,
    stop_mon: int,
    geo: str = "US",
    verbose: bool = True,
    wait_time: float = 60.0,
) -> pd.DataFrame:
    """
    Given a word, fetches daily search volume data from Google Trends and
    returns results in a pandas DataFrame.
    Details: Due to the way Google Trends scales and returns data, special
    care needs to be taken to make the daily data comparable over different
    months. To do that, we download daily data on a month by month basis,
    and also monthly data. The monthly data is downloaded in one go, so that
    the monthly values are comparable amongst themselves and can be used to
    scale the daily data. The daily data is scaled by multiplying the daily
    value by the monthly search volume divided by 100.

    For a more detailed explanation see http://bit.ly/trendsscaling

    Args:
        word (str): Word to fetch daily data for.
        start_year (int): the start year
        start_mon (int): start 1st day of the month
        stop_year (int): the end year
        stop_mon (int): end at the last day of the month
        geo (str): geolocation
        verbose (bool): If True, then prints the word and current time frame
            we are fecthing the data for.
    Returns:
        complete (pd.DataFrame): Contains 4 columns.
            The column named after the word argument contains the daily search
            volume already scaled and comparable through time.
            The column f'{word}_unscaled' is the original daily data fetched
            month by month, and it is not comparable across different months
            (but is comparable within a month).
            The column f'{word}_monthly' contains the original monthly data
            fetched at once. The values in this column have been backfilled
            so that there are no NaN present.
            The column 'scale' contains the scale used to obtain the scaled
            daily data.
    """
    # Set up start and stop dates
    start_date = date(start_year, start_mon, 1)
    stop_date = get_last_date_of_month(stop_year, stop_mon)

    # Start pytrends for US region
    pytrends = TrendReq()
    # Initialize build_payload with the word we need data for
    build_payload = partial(
        pytrends.build_payload, kw_list=[word], cat=0, geo=geo, gprop=""
    )

    # Obtain monthly data for all months in years [start_year, stop_year]
    monthly = _fetch_data(
        pytrends, build_payload, convert_dates_to_timeframe(start_date,
                                                            stop_date)
    )
    return monthly

In [ ]:
get_data(2020, 1, 2022, 8)

Task 0 (bis): Download some Media Cloud data using the explorer tool on the [Media Cloud website](https://explorer.mediacloud.org/#/home) and load it using pandas.

In [ ]:
mc_data = pd.read_csv(os.path.join("datasets", "mediacloud", "covid.csv"))
mc_data.head(5)

Task 1: Import the file NOR.csv. Apply the right preprocessing steps to replace the missing values.

In [6]:
df = pd.read_csv(os.path.join("datasets", "NOR.csv"))
df.head(5)

id        date  confirmed  deaths  recovered  tests  vaccines  \
0  2b1b6cf9  2020-01-22        NaN     NaN        NaN    NaN       NaN   
1  2b1b6cf9  2020-01-23        NaN     NaN        NaN    NaN       NaN   
2  2b1b6cf9  2020-01-24        NaN     NaN        NaN    NaN       NaN   
3  2b1b6cf9  2020-01-25        NaN     NaN        NaN    NaN       NaN   
4  2b1b6cf9  2020-01-26        NaN     NaN        NaN    NaN       NaN   

   people_vaccinated  people_fully_vaccinated  hosp  ...  iso_alpha_3  \
0                NaN                      NaN   NaN  ...          NOR   
1                NaN                      NaN   NaN  ...          NOR   
2                NaN                      NaN   NaN  ...          NOR   
3                NaN                      NaN   NaN  ...          NOR   
4                NaN                      NaN   NaN  ...          NOR   

   iso_alpha_2  iso_numeric  iso_currency  key_local  \
0           NO          578           NOK        NaN   
1           NO          578           NOK        NaN   
2           NO          578           NOK        NaN   
3           NO          578           NOK        NaN   
4           NO          578           NOK        NaN   

           key_google_mobility  key_apple_mobility  key_jhu_csse  key_nuts  \
0  ChIJv-VNj0VoEkYRK9BkuJ07sKE              Norway            NO       NaN   
1  ChIJv-VNj0VoEkYRK9BkuJ07sKE              Norway            NO       NaN   
2  ChIJv-VNj0VoEkYRK9BkuJ07sKE              Norway            NO       NaN   
3  ChIJv-VNj0VoEkYRK9BkuJ07sKE              Norway            NO       NaN   
4  ChIJv-VNj0VoEkYRK9BkuJ07sKE              Norway            NO       NaN   

   key_gadm  
0       NOR  
1       NOR  
2       NOR  
3       NOR  
4       NOR  

[5 rows x 47 columns]

In [7]:
# fillna forward and fillna 0 after
df.fillna(method="ffill", inplace=True)
df.fillna(0, inplace=True)

Task 2: Plot the cumulative & daily COVID-19 cases, deaths, and people vaccinated in Norway since 2020. Total: 6 figures.

In [13]:
daily = (df[["confirmed", "deaths", "people_vaccinated"]] - df[["confirmed", "deaths", "people_vaccinated"]].shift(1))[1:]
daily["date"] = df["date"][1:]  # add date

In [14]:
from plotly.subplots import make_subplots

fig = make_subplots(rows=2, cols=3)

# cumulative
fig.add_trace(go.Scatter(x=df["date"], y=df["confirmed"], mode="lines", name="confirmed"), row=1, col=1)
fig.add_trace(go.Scatter(x=df["date"], y=df["deaths"], mode="lines", name="deaths"), row=1, col=2)
fig.add_trace(go.Scatter(x=df["date"], y=df["people_vaccinated"], mode="lines", name="people_vaccinated"), row=1, col=3)
# daily
fig.add_trace(go.Scatter(x=daily["date"], y=daily["confirmed"], mode="lines", name="confirmed"), row=2, col=1)
fig.add_trace(go.Scatter(x=daily["date"], y=daily["deaths"], mode="lines", name="deaths"), row=2, col=2)
fig.add_trace(go.Scatter(x=daily["date"], y=daily["people_vaccinated"], mode="lines", name="people_vaccinated"), row=2, col=3)

fig.update_yaxes(title="Count")
fig.update_xaxes(title="Date")
fig.update_layout(title_text="COVID-19 pandemic over time")
fig.show()

Task 3: Similarly, explore some of the Media Cloud data (per region) and the Google Trends data (national).

In [27]:
# Load media cloud data
import glob


to_join = []
keywords_mc = []
for filename in glob.glob(os.path.join("datasets", "mediacloud", "*.csv")):
    keyword = filename.split("\\")[-1][:-4]  # keyword
    keywords_mc.append(keyword)
    to_join.append((keyword, pd.read_csv(filename)))  # load the dataframe
mc = to_join[0][1]  # first dataframe
mc.set_index("date", inplace=True)  # date as index
mc.index = pd.to_datetime(mc.index)  # datetime format
columns = [f"{to_join[0][0]}_{c}" for c in mc.columns]
mc.columns = columns  # rename the columns to add the keyword

# join all the keywords
for keyword, data in to_join[1:]:
    data.set_index("date", inplace=True)
    data.index = pd.to_datetime(data.index)
    columns = [f"{keyword}_{c}" for c in data.columns]
    data.columns = columns
    mc = mc.join(data)
mc.head(5)

covid_count_Oslo  covid_ratio_Oslo  covid_total_count_Oslo  \
date                                                                     
2020-01-01                 0               0.0                     181   
2020-01-02                 0               0.0                     283   
2020-01-03                 0               0.0                     252   
2020-01-04                 0               0.0                     201   
2020-01-05                 0               0.0                     188   

            covid_count_Hordaland  covid_ratio_Hordaland  \
date                                                       
2020-01-01                      0                    0.0   
2020-01-02                      0                    0.0   
2020-01-03                      0                    0.0   
2020-01-04                      0                    0.0   
2020-01-05                      0                    0.0   

            covid_total_count_Hordaland  covid_count_Akershus  \
date                                                            
2020-01-01                           32                     0   
2020-01-02                           46                     0   
2020-01-03                           61                     0   
2020-01-04                           29                     0   
2020-01-05                           36                     0   

            covid_ratio_Akershus  covid_total_count_Akershus  \
date                                                           
2020-01-01                   0.0                           7   
2020-01-02                   0.0                          12   
2020-01-03                   0.0                          23   
2020-01-04                   0.0                          13   
2020-01-05                   0.0                          10   

            covid_count_Aust-Agder  ...  vaksine_total_count_Telemark  \
date                                ...                                 
2020-01-01                       0  ...                             8   
2020-01-02                       0  ...                             8   
2020-01-03                       0  ...                            12   
2020-01-04                       0  ...                             6   
2020-01-05                       0  ...                             5   

            vaksine_count_Vest-Agder  vaksine_ratio_Vest-Agder  \
date                                                             
2020-01-01                         0                       0.0   
2020-01-02                         0                       0.0   
2020-01-03                         0                       0.0   
2020-01-04                         0                       0.0   
2020-01-05                         0                       0.0   

            vaksine_total_count_Vest-Agder  vaksine_count_Vestfold  \
date                                                                 
2020-01-01                              49                       0   
2020-01-02                              76                       0   
2020-01-03                              56                       0   
2020-01-04                              38                       0   
2020-01-05                              38                       0   

            vaksine_ratio_Vestfold  vaksine_total_count_Vestfold  \
date                                                               
2020-01-01                     0.0                             5   
2020-01-02                     0.0                             4   
2020-01-03                     0.0                             1   
2020-01-04                     0.0                             0   
2020-01-05                     0.0                             1   

            vaksine_count_National  vaksine_ratio_National  \
date                                                         
2020-01-01                       0                 0.00000   
2020-01-02                       0    

In [28]:
# extract region names
regions = list(set([c.split("_")[-1] for c in mc.columns]))
regions.remove("National")
regions.append("National")  # place National at the end
len(regions)

20

In [41]:
from plotly.colors import DEFAULT_PLOTLY_COLORS

# assign a color to each keyword
colors_dic = {}
for i, w in enumerate(keywords_mc):
    colors_dic[w] = DEFAULT_PLOTLY_COLORS[i % len(DEFAULT_PLOTLY_COLORS)]

cols = 3
rows = len(regions) // cols if (len(regions) % cols == 0) else (len(regions) // cols) + 1
fig = make_subplots(rows=rows, cols=cols, shared_xaxes=True, shared_yaxes=True, subplot_titles=regions)

for i, reg in enumerate(regions):
    for w in keywords_mc:
        fig.add_trace(go.Scatter(x=mc.index,
                                 y=mc[f"{w}_ratio_{reg}"],
                                 mode="lines",
                                 name=w,
                                 showlegend=(i==0),
                                 marker_color=colors_dic[w]),
                      row=(i//cols)+1,
                      col=(i%cols)+1)

fig.update_yaxes(range=(0, 0.5))
fig.update_yaxes(title="Ratio (cropped at 0.5)", row=1, col=1)
fig.update_xaxes(title="Date")
fig.update_layout(title_text="Media Cloud data (per regions and national)", height=1000)
fig.show()

In [44]:
# Load google trends data

to_join = []
keywords_gg = []
for filename in glob.glob(os.path.join("datasets", "googletrends", "*.csv")):
    keyword = filename.split("\\")[-1][:-4]  # keyword
    keywords_gg.append(keyword)
    to_join.append((keyword, pd.read_csv(filename)))  # load the dataframe
gg = to_join[0][1]  # first dataframe
gg.set_index("date", inplace=True)  # date as index
gg.index = pd.to_datetime(gg.index)  # datetime format
gg = gg[["Norway"]]  # remove monthly data
gg.columns = [to_join[0][0]]  # rename the column with the keyword

# join all the keywords
for keyword, data in to_join[1:]:
    data.set_index("date", inplace=True)
    data.index = pd.to_datetime(data.index)
    data = data[["Norway"]]  # remove monthly data
    data.columns = [keyword]  # rename the column with the keyword
    gg = gg.join(data)
gg.head(5)

covid  vaksinasjon
date                          
2020-01-01     89            0
2020-01-02      0            0
2020-01-03      0            0
2020-01-04      0          100
2020-01-05      0            0

In [45]:
# assign a color to each keyword that doesn't have a color
for i, w in enumerate(keywords_gg):
    if w not in colors_dic:
        colors_dic[w] = DEFAULT_PLOTLY_COLORS[i % len(DEFAULT_PLOTLY_COLORS)]

In [46]:
fig = go.Figure()

for w in keywords_gg:
    fig.add_trace(go.Scatter(x=gg.index,
                             y=gg[w],
                             mode="lines",
                             name=w,
                             marker_color=colors_dic[w]))

fig.update_yaxes(range=(0, 100))
fig.update_yaxes(title="Score")
fig.update_xaxes(title="Date")
fig.update_layout(title_text="Google Trends data (national)")
fig.show()